In [1]:
import camelot
import pandas as pd
import openpyxl
import os
# tables = camelot.read_pdf('epd1388_2021.pdf', pages='10',process_background=True)
# tables = camelot.read_pdf('./IBU-09-20/New/14632.pdf', pages='6', split_text=True,table_areas=["69.60548391889084,500.088593765987,525.3099336281931,403.96614296894364"])
# print(len(tables))

# tables = camelot.read_pdf('./New/14699.pdf', pages='all')
# print(len(tables))

In [2]:
headers = [
    'impactGWP100_kgCO2e_total',
    'impactGWP100_kgCO2e_fossil',
    'impactGWP100_kgCO2e_biogenic' ,
    'impactGWP100_kgCO2e_luluc' ,
    'impactODP_WMO2014_kgCFC11e' ,
    'impactAP_molHeq' ,
    'impactEPFreshwater_kgPO4e' ,
    'impactEPFreshwater_kgP' ,
    'impactEPMarine_kgNe' ,
    'impactEPTerrestrial_molNe' ,
    'impactPOCP_kgNMVOCe' ,
    'cleanWaterDeprivation_m3' ,
    'particulateMatter_incidence' ,
    'ionisingRadiation_kgU235eq' ,
    'ecoToxicityFreshwater_CTUe' ,
    'humanToxicityCancer_CTUh' ,
    'humanToxicityNonCancer_CTUh' ,
    'potentialSoilQualityIndex' ,
    "impactADPElements_kgSbe" ,
    "impactADPFossilFuels_MJ" ,
    
    "renewablesUsedAsEnergy_MJ",
    "renewablesUsedAsMaterial_MJ",
    "embodiedRenewableEnergy_MJ",
    "nonRenewablesUsedAsEnergy_MJ",
    "nonRenewablesUsedAsMaterial_MJ",
    "embodiedEnergy_MJ",
    
    "recyclingMaterialUse_kg",
    "renewableRecylingFuelUse_MJ",
    "nonRenewableRecylingFuelUse_MJ",
    "cleanWaterNetUse_m3",
    "wasteHazardous_kg",
    "wasteNonHazardous_kg",
    "wasteRadioactive_kg",
    "reusableMaterialsOutput_kg",
    "recyclableMaterialsOutput_kg",
    "energyMaterialsOutput_kg",
    "exportedEnergyOutput_MJ_thermal",
    "exportedEnergyOutput_MJ_electric",
    "exportedEnergyOutput_MJ",
    
    "traciGWP_kgCO2e",
    "traciODP_kgCFC11e",
    "traciAP_kgSO2e",
    "traciEP_kgNe",
    "traciPOCP_kgO3e",
    "traciNRPE_MJ"
]
columns = {
'impactGWP100_kgCO2e_total':'(^GWP - Total$)',
'impactGWP100_kgCO2e_fossil':'(^GWP - Fossil$)',
'impactGWP100_kgCO2e_biogenic':'(^GWP - Biogenic$)',
'impactGWP100_kgCO2e_luluc':'(^GWP - Luluc$)',
'impactODP_WMO2014_kgCFC11e':'(^ODP$)',
'impactAP_molHeq':'(^AP$)',
'impactEPFreshwater_kgPO4e':'(^\*EP - Freshwater$)',
'impactEPFreshwater_kgP':'(^EP - Freshwater$)',
'impactEPMarine_kgNe':'(^EP - Marine$)',
'impactEPTerrestrial_molNe':'(^EP - Terrestrial$)',
'impactPOCP_kgNMVOCe':'(^POCP$)',
'cleanWaterDeprivation_m3':'(^WDP$)',
'particulateMatter_incidence':'(^PM$)',
'ionisingRadiation_kgU235eq':'(^IR$)',
'ecoToxicityFreshwater_CTUe':'(^ETP - FW$)',
'humanToxicityCancer_CTUh':'(^HTTP - C$)',
'humanToxicityNonCancer_CTUh':'(^HTTP - NC$)',
'potentialSoilQualityIndex':'(^SQP$)',
"impactADPElements_kgSbe": "(^ADPE$)",
"impactADPFossilFuels_MJ": "(^ADPF$)",
    
  "renewablesUsedAsEnergy_MJ": "(^PERE$)|(^Erneuerbare Primärenergie als Energieträger$)|(^Renewable primary energy as energy carrier$)",
  "renewablesUsedAsMaterial_MJ": "(^PERM$)|(^Erneuerbare Primärenergie zur stofflichen Nutzung$)|(^Renewable primary energy resources as material utilization$)",
  "embodiedRenewableEnergy_MJ": "(^PERT$)|(^Total erneuerbare Primärenergie$)|(^Total use of renewable primary energy resources$)",
  "nonRenewablesUsedAsEnergy_MJ": "(^PENRE$)|(^Nicht-erneuerbare Primärenergie als Energieträger$)|(^Nicht\xaderneuerbare Primärenergie als Energieträger$)|(^Non-renewable primary energy as energy carrier$)",
  "nonRenewablesUsedAsMaterial_MJ": "(^PENRM$)|(^Nicht-erneuerbare Primärenergie zur stofflichen Nutzung$)|(^Nicht\xaderneuerbare Primärenergie zur stofflichen Nutzung$)|(^Non-renewable primary energy as material utilization$)",
  "embodiedEnergy_MJ": "(^PENRT$)|(^Total nicht erneuerbare Primärenergie$)|(^Total use of non-renewable primary energy resources$)",
  "recyclingMaterialUse_kg": "(^SM$)|(^Einsatz von Sekundärstoffen$)|(^Use of secondary material$)",
  "renewableRecylingFuelUse_MJ": "(^RSF$)|(^Erneuerbare Sekundärbrennstoffe$)|(^Use of renewable secondary fuels$)",
  "nonRenewableRecylingFuelUse_MJ": "(^NRSF$)|(^Nicht-erneuerbare Sekundärbrennstoffe$)|(^Nicht\xaderneuerbare Sekundärbrennstoffe$)|(^Use of non-renewable secondary fuels$)",
  "cleanWaterNetUse_m3": "(^FW$)|(^Nettoeinsatz von Süßwasserressourcen$)|(^Use of net fresh water$)",
    
  "wasteHazardous_kg": "(^HWD$)|(^Gefährlicher Abfall zur Deponie$)|(^Hazardous waste disposed$)",
  "wasteNonHazardous_kg": "(^NHWD$)|(^Entsorgter nicht gefährlicher Abfall$)|(^Non-hazardous waste disposed$)",
  "wasteRadioactive_kg": "(^RWD$)|(^Entsorgter radioaktiver Abfall$)|(^Radioactive waste disposed$)",
  "reusableMaterialsOutput_kg": "(^CRU$)|(^Komponenten für die Wiederverwendung$)|(^Components for re-use$)",
  "recyclableMaterialsOutput_kg": "(^MFR$)|(^Stoffe zum Recycling$)|(^Materials for recycling$)",
  "energyMaterialsOutput_kg": "(^MER$)|(^Stoffe für die Energierückgewinnung)|(^Materials for energy recovery$)",
  "exportedEnergyOutput_MJ_electric": "(^EE \(Electrical\))|(^Exportierte elektrische Energie$)|(^Exported electrical energy$)",
  "exportedEnergyOutput_MJ_thermal": "(^EE \(Thermal\)$)|(^Exportierte thermische Energie$)|(^Exported thermal energy$)",
  "exportedEnergyOutput_MJ": "(^EE$)",
    
  "traciGWP_kgCO2e": 8,
  "traciODP_kgCFC11e": 12,
  "traciAP_kgSO2e": 6,
  "traciEP_kgNe": 7,
  "traciPOCP_kgO3e": 10,
  "traciNRPE_MJ": 17
}

In [3]:
def get_epd_number(file_name):
    tables = camelot.read_pdf('./4/' + file_name , pages='1', flavor='stream')
    return tables[0].df[1][3]

In [4]:
def make_excel_file(files_data):
    book = openpyxl.Workbook()
    filename = 'test_ibu.xlsx'
    book.save(filename)

    sheet = book['Sheet']
    sheet.cell(row=1, column=1).value = 'Filename'
    sheet.cell(row=1, column=2).value = 'EPD_Number'
    sheet.cell(row=1, column=3).value = 'DownloadLink'
    sheet.cell(row=1, column=4).value = 'Stages'
    
    count = 5
    for header in headers:
        sheet.cell(row=1, column=count).value = header
        count += 1
    
    current_row = 2
    for file_data in files_data:
        dataFrames = file_data["dataFrame"]
        base_added = False
        
        for stage in file_data["stages"]:
            if not base_added:
                sheet.cell(row=current_row, column=1).value = file_data["file_name"]
                sheet.cell(row=current_row, column=2).value = get_epd_number(file_data["file_name"])
                sheet.cell(row=current_row, column=3).value = '/mnt/data/Downloads/2021-10-18/IBU/New/' + file_data["file_name"]
                base_added = True

            sheet.cell(row=current_row, column=4).value = stage
            header_counter = 0
            for header in headers:
                for df in dataFrames:                    
                    try:
                        if header == 'exportedEnergyOutput_MJ':
                            replaced_eee = df[df['Impact \nCategory'].str.contains(columns["exportedEnergyOutput_MJ_electric"])][stage].to_list()[0].replace(',', '.')
                            if not replaced_eee == 'IND':
                                try:
                                    value_eee = float(replaced_eee)
                                except:
                                    value_eee = float(replaced_eee.replace('\xad', '-'))
                            else:
                                value_eee = replaced_eee
                                
                            replaced_eet = df[df['Impact \nCategory'].str.contains(columns["exportedEnergyOutput_MJ_electric"])][stage].to_list()[0].replace(',', '.')
                            if not replaced_eet == 'IND':
                                try:
                                    value_eet = float(replaced_eet)
                                except:
                                    value_eet = float(replaced_eet.replace('\xad', '-'))
                            else:
                                value_eet = replaced_eet
                            value = value_eet + value_eee
                            sheet.cell(row=current_row, column= 5 + header_counter).number_format = '0.000E+00'
                            sheet.cell(row=current_row, column= 5 + header_counter).value = value
                        else:
                            sheet.cell(row=current_row, column= 5 + header_counter).number_format = '0.000E+00'
                            replaced = df[df['Impact \nCategory'].str.contains(columns[header])][stage].to_list()[0].replace(',', '.')
                            if not replaced == 'IND':
                                try:
                                    value = float(replaced)
                                except:
                                    value = float(replaced.replace('\xad', '-'))
                            else:
                                value = replaced

                            #value = float(df[df.eq(columns[header]).any(1)][i].to_list()[0])
                            sheet.cell(row=current_row, column= 5 + header_counter).value = value
                    except:
                        print("**************************************ERRROR*****************************")
                        print(file_data["file_name"])
                        print(stage)
                        print(columns[header])
                        
                header_counter= header_counter +1
            current_row = current_row + 1
        current_row = current_row + 1
            
    book.save(filename)
    book.close()

In [5]:
files = os.listdir('./4')
#files = ['epd4044.pdf', 'epd4051.pdf', 'epd4054.pdf','epd4061.pdf']

r = []
for file in files:
    tables = camelot.read_pdf('./4/' + file, pages='all')
    print("************ FILE NAME: " + file + " ****************")
    dataFrames = []
    file_info = {}
    stages = []
    for table in tables:
        df = table.df

        #dataFrames = []
        gwp = ['GWP-total', 'GWP - Total', 'Global warming potential', 'GWP', 'Globales Erwärmungspotenzial ­ total', 'Globales Erwärmungspotenzial']
        for g in gwp:
            if (g in df.values) and ('TRACI 2.1 Impact Assessment' not in df.values):
                df = df.rename(columns=df.iloc[0])
                dataFrames.append(df)


        pere = ['PERE', 'Renewable primary energy as energy carrier', 'Erneuerbare Primärenergie als Energieträger']
        for p in pere:
            if p in df.values:
                df = df.rename(columns=df.iloc[0])
                dataFrames.append(df)

        hwd = ['HWD', 'Hazardous waste disposed', 'Gefährlicher Abfall zur Deponie']
        for h in hwd:
            if h in df.values:
                df = df.rename(columns=df.iloc[0])
                dataFrames.append(df)


    try:
        rez = []
        for list in df[df.eq('Unit').any(1)].values:
            rez = rez + list.tolist()
        longest_list = []
        help = [longest_list.append(x) for x in rez if x not in longest_list]

        droped_nan = [e for e in longest_list if str(e) != 'nan']


        unit_index = droped_nan.index('Unit') + 1
        stages = droped_nan[unit_index:]
        print(stages)
    except:
        a = list(df[df.eq('Einheit').any(1)].values[0])
        unit_index = a.index('Einheit') + 1
        stages = a[unit_index:]




                
    #result = pd.concat(dataFrames)
    file_info["dataFrame"] = dataFrames        
    file_info["file_name"] = file
    file_info["stages"] = stages
    
    r.append(file_info)
    
    #write_to_excel(dataFrame, stages)

make_excel_file(r)

# print(types)
# r

************ FILE NAME: epd4040.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4041.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4042.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4043.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4044.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4045.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4046.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4047.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4048.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4049.pdf ****************
['A1-A3', '

************ FILE NAME: epd4067.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4068.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4069.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4070.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4071.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4072.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4073.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4074.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
************ FILE NAME: epd4075.pdf ****************
['A1-A3', 'A4', 'A5', 'C1', 'C2', 'C3', 'C4', 'D']
**************************************ERRROR********************

C:\Users\mirol\anaconda3\lib\site-packages\pandas\core\strings\accessor.py:101: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  return func(self, *args, **kwargs)



epd4040.pdf
A1-A3
(^\*EP - Freshwater$)
**************************************ERRROR*****************************
epd4040.pdf
A1-A3
(^\*EP - Freshwater$)
**************************************ERRROR*****************************
epd4040.pdf
A1-A3
(^EP - Freshwater$)
**************************************ERRROR*****************************
epd4040.pdf
A1-A3
(^EP - Freshwater$)
**************************************ERRROR*****************************
epd4040.pdf
A1-A3
(^EP - Marine$)
**************************************ERRROR*****************************
epd4040.pdf
A1-A3
(^EP - Marine$)
**************************************ERRROR*****************************
epd4040.pdf
A1-A3
(^EP - Terrestrial$)
**************************************ERRROR*****************************
epd4040.pdf
A1-A3
(^EP - Terrestrial$)
**************************************ERRROR*****************************
epd4040.pdf
A1-A3
(^POCP$)
**************************************ERRROR*****************************
epd4

**************************************ERRROR*****************************
epd4040.pdf
C1
(^GWP - Biogenic$)
**************************************ERRROR*****************************
epd4040.pdf
C1
(^GWP - Biogenic$)
**************************************ERRROR*****************************
epd4040.pdf
C1
(^GWP - Luluc$)
**************************************ERRROR*****************************
epd4040.pdf
C1
(^GWP - Luluc$)
**************************************ERRROR*****************************
epd4040.pdf
C1
(^ODP$)
**************************************ERRROR*****************************
epd4040.pdf
C1
(^ODP$)
**************************************ERRROR*****************************
epd4040.pdf
C1
(^AP$)
**************************************ERRROR*****************************
epd4040.pdf
C1
(^AP$)
**************************************ERRROR*****************************
epd4040.pdf
C1
(^\*EP - Freshwater$)
**************************************ERRROR*****************************
epd

...

**************************************ERRROR*****************************
epd4074.pdf
D
(^EE \(Thermal\)$)|(^Exportierte thermische Energie$)|(^Exported thermal energy$)
**************************************ERRROR*****************************
epd4074.pdf
D
(^EE \(Thermal\)$)|(^Exportierte thermische Energie$)|(^Exported thermal energy$)
**************************************ERRROR*****************************
epd4074.pdf
D
(^EE \(Electrical\))|(^Exportierte elektrische Energie$)|(^Exported electrical energy$)
**************************************ERRROR*****************************
epd4074.pdf
D
(^EE \(Electrical\))|(^Exportierte elektrische Energie$)|(^Exported electrical energy$)
**************************************ERRROR*****************************
epd4074.pdf
D
(^EE$)
**************************************ERRROR*****************************
epd4074.pdf
D
(^EE$)
**************************************ERRROR*****************************
epd4074.pdf
D
8
****************************

C:\Users\mirol\anaconda3\lib\site-packages\pandas\core\strings\accessor.py:101: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  return func(self, *args, **kwargs)



epd4075.pdf
A1-A3
(^PM$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^IR$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^IR$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^ETP - FW$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^ETP - FW$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^HTTP - C$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^HTTP - C$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^HTTP - NC$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^HTTP - NC$)
**************************************ERRROR*****************************
epd4075.pdf
A1-A3
(^SQP$)
**************************************ERRROR

C1
(^IR$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^ETP - FW$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^ETP - FW$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^HTTP - C$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^HTTP - C$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^HTTP - NC$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^HTTP - NC$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^SQP$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^SQP$)
**************************************ERRROR*****************************
epd4075.pdf
C1
(^ADPE$)
**************************************ERRROR*****************************
epd4075.pd

C3
(^EE$)
**************************************ERRROR*****************************
epd4075.pdf
C3
8
**************************************ERRROR*****************************
epd4075.pdf
C3
8
**************************************ERRROR*****************************
epd4075.pdf
C3
8
**************************************ERRROR*****************************
epd4075.pdf
C3
12
**************************************ERRROR*****************************
epd4075.pdf
C3
12
**************************************ERRROR*****************************
epd4075.pdf
C3
12
**************************************ERRROR*****************************
epd4075.pdf
C3
6
**************************************ERRROR*****************************
epd4075.pdf
C3
6
**************************************ERRROR*****************************
epd4075.pdf
C3
6
**************************************ERRROR*****************************
epd4075.pdf
C3
7
**************************************ERRROR*****************************
epd

In [20]:
test_df = r[5]['dataFrame'][2]

In [25]:
test_df['Impact \nCategory'][8]


'EE (Thermal)'

In [34]:
test_df[test_df['Impact \nCategory'].str.contains("^EE \(Electrical\)")]

Impact \nCategory Unit A1-A3 A4 A5 C1 C2 C3 C4  D
7   EE (Electrical)   MJ     0  0  0  0  0  0  0  0

In [ ]:
'potentialSoilQualityIndex':'(^SQP$)',
"impactADPElements_kgSbe": "(^ADPE$) ",
"impactADPFossilFuels_MJ": "(^ADPF$) ",